## CAB420 Final Assignment
### Author: KA LONG LEE ( N9845097 )

# Importing Library and Read Data from CSV files


In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import random

# Spliting data to trainning and testing set
from sklearn.model_selection import train_test_split
# Fitting Multiple Linear Regression to the trainning set
from sklearn.linear_model import LinearRegression, Lasso
from sklearn.cluster import KMeans
from sklearn.metrics import mean_squared_error, r2_score, classification_report, confusion_matrix,accuracy_score

# Matplotlib setting 
%config InlineBackend.print_figure_kwargs = {'bbox_inches':None}
%config InlineBackend.rc = {'font.size': 30, 'figure.figsize': (30.0, 20.0), 'figure.facecolor': (1, 1, 1, 0), 'figure.subplot.bottom': 0.125, 'figure.edgecolor': (1, 1, 1, 0), 'figure.dpi': 500}

## Data Preprocessing

In [2]:
def convert_dummy_movie_dataset():
    movies_dataset = pd.read_csv("./data/movies.csv")
                             
    # Set the index by movieId, This line of code only able to execute once
    movies_dataset.set_index('movieId', inplace = True)
                             
    # Convert genres to dummy variable dataset
    # movies_genres_dummy <- a dataframe contains the genres values for all the movies and using movieId as index
    movies_genres_dummy = movies_dataset['genres'].str.get_dummies(sep='|')
    # Remove (no genres listed) from dummy because all 0 can represent (no genres listed)
    movies_genres_dummy = movies_genres_dummy.drop(columns=["(no genres listed)"], axis=1)

    # Pre Processing for KMeans Algorithm finding the similar movies
    movies_dataset = movies_dataset.drop(columns=["genres"], axis=1)
    movies_dataset = pd.merge(movies_dataset, movies_genres_dummy, on = 'movieId', how = "left")
                             
    return movies_dataset.drop(columns=["title"], axis=1)

def generate_rating_dataset_With_avg_rating():
    # Import dataset
    rating_dataset = pd.read_csv("./data/ratings.csv")
    
    user_avg_rating = rating_dataset.groupby('userId')['rating'].mean().to_frame()
    user_avg_rating = user_avg_rating.rename(columns={"rating": "user_avg_rating"})

    movie_avg_rating = rating_dataset.groupby('movieId')['rating'].mean().to_frame()
    movie_avg_rating = movie_avg_rating.rename(columns={"rating": "movie_avg_rating"})

    rating_dataset = pd.merge(rating_dataset, user_avg_rating, on = 'userId', how = "left")
    rating_dataset = pd.merge(rating_dataset, movie_avg_rating, on = 'movieId', how = "left")

    return rating_dataset.drop(columns=["timestamp"], axis=1)

def get_movie_genres():
    return convert_dummy_movie_dataset().columns

def get_tags_df():
    tags_dataset = pd.read_csv("./data/tags.csv")
    tags_dataset['tag'] = tags_dataset['tag'].str.lower()
    # Currently we disable the userId
    return pd.get_dummies(tags_dataset).drop(columns=["timestamp", "userId"],axis=1)

def generate_full_dataset():
    movie_df = convert_dummy_movie_dataset();
    tags_df = get_tags_df();
    # Merge Three dataset, tags + movie + rating, to the complete dataset
    full_rating_dataset = pd.merge(rating_df, movie_df, on = 'movieId', how = "left")

    # Merge user average rating for each genre to the dataframe    
    for genre in get_movie_genres():
        user_avg_genre_rating = full_rating_dataset.loc[(full_rating_dataset[genre] == 1)].groupby('userId')['rating'].mean().to_frame()
        user_avg_genre_rating = user_avg_genre_rating.rename(columns={"rating": "user_avg_"+ genre +"_rating"})
        full_rating_dataset = pd.merge(full_rating_dataset, user_avg_genre_rating, on = 'userId', how = "left")

    # return the non zero result dataframe
    return pd.merge(full_rating_dataset, tags_df, on = 'movieId', how = "left").fillna(0)


## Movie Dataframe

In [3]:
movie_df = convert_dummy_movie_dataset();
movie_df.head()

Action  Adventure  Animation  Children  Comedy  Crime  Documentary  \
movieId                                                                       
1             0          1          1         1       1      0            0   
2             0          1          0         1       0      0            0   
3             0          0          0         0       1      0            0   
4             0          0          0         0       1      0            0   
5             0          0          0         0       1      0            0   

         Drama  Fantasy  Film-Noir  Horror  IMAX  Musical  Mystery  Romance  \
movieId                                                                       
1            0        1          0       0     0        0        0        0   
2            0        1          0       0     0        0        0        0   
3            0        0          0       0     0        0        0        1   
4            1        0          0       0     0        0        0        1   
5            0        0          0       0     0        0        0        0   

         Sci-Fi  Thriller  War  Western  
movieId                                  
1             0         0    0        0  
2             0         0    0        0  
3             0         0    0        0  
4             0         0    0        0  
5             0         0    0        0

## Rating Dataframe

In [4]:
rating_df = generate_rating_dataset_With_avg_rating();
rating_df.head()

userId  movieId  rating  user_avg_rating  movie_avg_rating
0       1        1     4.0         4.366379          3.920930
1       1        3     4.0         4.366379          3.259615
2       1        6     4.0         4.366379          3.946078
3       1       47     5.0         4.366379          3.975369
4       1       50     5.0         4.366379          4.237745

## Tags Dataframe

In [5]:
tags_df = get_tags_df()
tags_df.head()

movieId  tag_"artsy"  tag_06 oscar nominated best movie - animation  \
0    60756            0                                              0   
1    60756            0                                              0   
2    60756            0                                              0   
3    89774            0                                              0   
4    89774            0                                              0   

   tag_1900s  tag_1920s  tag_1950s  tag_1960s  tag_1970s  tag_1980s  \
0          0          0          0          0          0          0   
1          0          0          0          0          0          0   
2          0          0          0          0          0          0   
3          0          0          0          0          0          0   
4          0          0          0          0          0          0   

   tag_1990s  ...  tag_world war i  tag_world war ii  tag_writing  \
0          0  ...                0                 0            0   
1          0  ...                0                 0            0   
2          0  ...                0                 0            0   
3          0  ...                0                 0            0   
4          0  ...                0                 0            0   

   tag_wrongful imprisonment  tag_wry  tag_younger men  tag_zither  \
0                          0        0                0           0   
1                          0        0                0           0   
2                          0        0                0           0   
3                          0        0                0           0   
4                          0        0                0           0   

   tag_zoe kazan  tag_zombies  tag_zooey deschanel  
0              0            0                    0  
1              0            0                    0  
2              0            0                    0  
3              0            0                    0  
4              0            0                    0  

[5 rows x 1476 columns]

## Full information Dataset (rating + tags + movies)

In [28]:
full_rating_dataset = generate_full_dataset()
# full_rating_dataset.to_csv("./data/full_rating.csv")
full_rating_dataset

userId  movieId  rating  user_avg_rating  movie_avg_rating  Action  \
0            1        1     4.0         4.366379          3.920930       0   
1            1        1     4.0         4.366379          3.920930       0   
2            1        1     4.0         4.366379          3.920930       0   
3            1        3     4.0         4.366379          3.259615       0   
4            1        3     4.0         4.366379          3.259615       0   
5            1        6     4.0         4.366379          3.946078       1   
6            1       47     5.0         4.366379          3.975369       0   
7            1       47     5.0         4.366379          3.975369       0   
8            1       47     5.0         4.366379          3.975369       0   
9            1       50     5.0         4.366379          4.237745       0   
10           1       50     5.0         4.366379          4.237745       0   
11           1       50     5.0         4.366379          4.237745       0   
12           1       50     5.0         4.366379          4.237745       0   
13           1       50     5.0         4.366379          4.237745       0   
14           1       50     5.0         4.366379          4.237745       0   
15           1       70     3.0         4.366379          3.509091       1   
16           1      101     5.0         4.366379          3.782609       0   
17           1      101     5.0         4.366379          3.782609       0   
18           1      101     5.0         4.366379          3.782609       0   
19           1      110     4.0         4.366379          4.031646       1   
20           1      110     4.0         4.366379          4.031646       1   
21           1      110     4.0         4.366379          4.031646       1   
22           1      110     4.0         4.366379          4.031646       1   
23           1      110     4.0         4.366379          4.031646       1   
24           1      110     4.0         4.366379          4.031646       1   
25           1      110     4.0         4.366379          4.031646       1   
26           1      110     4.0         4.366379          4.031646       1   
27           1      110     4.0         4.366379          4.031646       1   
28           1      110     4.0         4.366379          4.031646       1   
29           1      151     5.0         4.366379          3.545455       1   
...        ...      ...     ...              ...               ...     ...   
285732     610   160836     3.0         3.688556          3.000000       1   
285733     610   161582     4.0         3.688556          3.562500       0   
285734     610   161634     4.0         3.688556          3.300000       0   
285735     610   162350     3.5         3.688556          3.583333       1   
285736     610   163937     3.5         3.688556          3.500000       0   
285737     610   163981     3.5         3.688556          3.500000       0   
285738     610   164179     5.0         3.688556          3.980769       0   
285739     610   164179     5.0         3.688556          3.980769       0   
285740     610   164179     5.0         3.688556          3.980769       0   
285741     610   164179     5.0         3.688556          3.980769       0   
285742     610   164179     5.0         3.688556          3.980769       0   
285743     610   164179     5.0         3.688556          3.980769       0   
285744     610   164179     5.0         3.688556          3.980769       0   
285745     610   166528     4.0         3.688556          3.925926       1   
285746     610   166534     4.0         3.688556          3.333333       0   
285747     610   168248     5.0         3.688556          4.142857       1   
285748     610   168248     5.0         3.688556          4.142857       1   
285749     610   168248     5.0         3.688556          4.142857       1   
285750     610   168248     5.0         3.688556          4.142857       1   
285751     610   168248     5.

In [7]:
from sklearn.utils import shuffle
full_rating_dataset = shuffle(full_rating_dataset)

full_rating_dataset

userId  movieId  rating  user_avg_rating  movie_avg_rating  Action  \
11443       23     1089     4.0         3.648760          4.202290       0   
157560     345      924     4.0         3.903226          3.894495       0   
174080     380   113278     3.0         3.673235          3.000000       1   
281370     608      296     5.0         3.134176          4.197068       0   
33173       68     5400     3.5         3.233730          2.970588       0   
194331     420      541     3.5         3.822695          4.100806       1   
211441     458      296     4.0         4.152542          4.197068       0   
91887      211     2959     5.0         3.904494          4.272936       1   
68656      153   168492     4.5         2.217877          3.750000       0   
254562     564     5299     3.5         3.579618          3.266667       0   
143557     317      296     5.0         3.730159          4.197068       0   
145100     318     4034     3.5         3.755973          3.900000       0   
197804     428      260     3.5         2.640000          4.231076       1   
60575      132     6874     4.5         3.038905          3.961832       1   
221313     476      296     3.0         3.681159          4.197068       0   
250844     560      296     4.0         3.567686          4.197068       0   
148529     326      296     4.0         4.016447          4.197068       0   
281023     607     3081     4.0         3.786096          3.475806       0   
77248      177     8808     3.5         3.375553          2.500000       0   
57689      125    69757     1.0         3.859722          3.666667       0   
170774     376     1101     4.0         4.063910          3.301205       1   
152382     332     1203     4.0         3.599251          4.149123       0   
270152     599      904     3.0         2.642050          4.261905       0   
262316     583    71535     3.0         3.294643          3.877358       1   
56248      123      296     4.0         4.035714          4.197068       0   
72396      166      296     4.5         4.073684          4.197068       0   
246097     546      104     4.0         3.437500          3.439394       0   
105336     234     4226     4.0         3.504950          4.122642       0   
272453     599    45499     2.5         2.642050          3.355769       1   
271048     599     2959     5.0         2.642050          4.272936       1   
...        ...      ...     ...              ...               ...     ...   
176259     384      296     5.0         3.085714          4.197068       0   
80637      182     4370     3.0         3.511259          3.339286       0   
151259     330    79132     5.0         3.690283          4.066434       1   
134724     301      296     4.5         3.320175          4.197068       0   
58983      130      296     4.0         3.535714          4.197068       0   
111880     249    68954     3.5         3.696463          4.004762       0   
237548     516      457     4.0         3.692308          3.992105       0   
49029      105    71899     4.0         4.116343          4.200000       0   
43638       95     1089     5.0         4.062500          4.202290       0   
191757     415      922     4.5         4.085106          4.333333       0   
53936      119      293     5.0         4.176744          4.018797       1   
216772     471      296     4.0         3.875000          4.197068       0   
257687     571     1994     3.0         2.571429          3.425532       0   
112024     249    80463     4.0         3.696463          3.885965       0   
80379      182     3185     4.0         3.511259          3.333333       0   
267436     594     6373     5.0         3.924569          3.316901       0   
54861      121      296     4.0         3.293103          4.197068       0   
106032     239      293     4.5         4.026882          4.018797       1   
140589     308    68358     4.0         2.426087          3.864407       1   
104386     233      296     4.

In [8]:
X_df = full_rating_dataset.drop(columns=['rating'], axis=1)
y_df = full_rating_dataset.loc[:,'rating'].astype(str)

X = X_df.values
y = y_df.values

## Random Forest Algorithm

In [9]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score, cross_val_predict

X_train, X_test, y_train, y_test = train_test_split(X,y, test_size = 0.3)

rfc = RandomForestClassifier(n_estimators=100)

rfc.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=None,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False)

In [10]:
rfc.score(X,y)

0.9392431463945521

In [11]:
rfc.score(X_test,y_test)

0.7974780995929032

In [12]:
yhat = rfc.predict(X_test)

yhat

array(['4.0', '3.0', '5.0', ..., '5.0', '5.0', '3.0'], dtype=object)

In [13]:
y_test

array(['4.0', '3.0', '5.0', ..., '5.0', '5.0', '3.0'], dtype=object)

In [14]:
print(classification_report(y_test,yhat))

              precision    recall  f1-score   support

         0.5       0.77      0.71      0.74       847
         1.0       0.75      0.60      0.67      1695
         1.5       0.61      0.46      0.53       870
         2.0       0.66      0.57      0.61      3908
         2.5       0.65      0.58      0.61      3025
         3.0       0.70      0.72      0.71     12147
         3.5       0.73      0.73      0.73      9044
         4.0       0.79      0.84      0.81     23217
         4.5       0.89      0.84      0.86     10539
         5.0       0.91      0.91      0.91     20437

   micro avg       0.80      0.80      0.80     85729
   macro avg       0.75      0.70      0.72     85729
weighted avg       0.80      0.80      0.80     85729



## Naive Bayes Gaussian Models

In [15]:
df = pd.merge(rating_df, movie_df, on = 'movieId', how = "left")
df = pd.merge(df, tags_df, on = 'movieId', how = "left").fillna(0)

NB_X = df.drop(columns=['user_avg_rating','movie_avg_rating','rating'], axis=1)
NB_y = df['rating'].astype(str)

NB_X.columns

Index(['userId', 'movieId', 'Action', 'Adventure', 'Animation', 'Children',
       'Comedy', 'Crime', 'Documentary', 'Drama',
       ...
       'tag_world war i', 'tag_world war ii', 'tag_writing',
       'tag_wrongful imprisonment', 'tag_wry', 'tag_younger men', 'tag_zither',
       'tag_zoe kazan', 'tag_zombies', 'tag_zooey deschanel'],
      dtype='object', length=1496)

In [16]:
from sklearn.naive_bayes import GaussianNB
X_train, X_test, y_train, y_test = train_test_split( NB_X.values, NB_y.values , test_size = 0.2)

clf = GaussianNB()

clf.fit(X_train, y_train)

clf.score(X_train, y_train)

0.27312135567716056

In [17]:
clf.score(X_test, y_test)

0.2736514268717303

In [18]:
yhat = clf.predict(X_test)

In [19]:
print(classification_report(y_test,yhat))

/usr/local/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

         0.5       0.00      0.00      0.00       618
         1.0       0.00      0.00      0.00      1092
         1.5       0.03      0.02      0.03       576
         2.0       0.00      0.00      0.00      2609
         2.5       0.00      0.00      0.00      2034
         3.0       0.00      0.00      0.00      8072
         3.5       0.17      0.09      0.12      6089
         4.0       0.28      0.38      0.33     15460
         4.5       0.00      0.00      0.00      7020
         5.0       0.28      0.67      0.40     13583

   micro avg       0.27      0.27      0.27     57153
   macro avg       0.08      0.12      0.09     57153
weighted avg       0.16      0.27      0.20     57153



# K-Means Algorithm Clustering Similar Movies

In [20]:
# The dataset will use in this case
movie_df.iloc[:,1:-3].head()

movie_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9742 entries, 1 to 193609
Data columns (total 19 columns):
Action         9742 non-null int64
Adventure      9742 non-null int64
Animation      9742 non-null int64
Children       9742 non-null int64
Comedy         9742 non-null int64
Crime          9742 non-null int64
Documentary    9742 non-null int64
Drama          9742 non-null int64
Fantasy        9742 non-null int64
Film-Noir      9742 non-null int64
Horror         9742 non-null int64
IMAX           9742 non-null int64
Musical        9742 non-null int64
Mystery        9742 non-null int64
Romance        9742 non-null int64
Sci-Fi         9742 non-null int64
Thriller       9742 non-null int64
War            9742 non-null int64
Western        9742 non-null int64
dtypes: int64(19)
memory usage: 1.5 MB


In [21]:
# X only contains movie genres values
X = movie_df.iloc[:,1:-3].values

# Performs K = 1 to 50 for clustering the data
Ks = range(1,50)
# Array for saving inertias values for each K Clustering
inertias = []

# Loop K times 
for k in Ks:
    # Create KMeans
    model = KMeans(n_clusters = k)
    # Train KMeans 
    model.fit(X)
    inertias.append(model.inertia_)

# Plot inertias values vs K numbers 
plt.ylabel("inertias")
plt.xlabel("Numbers of K")
plt.plot(Ks,inertias,'-o')

## We Can see the result from the graph. The numbers of Inertias are dramatically decreased when k= 1 to k = 20, from 16000 to 6000. Then it becomes slow, from 6000 to 4000 when k = 21 to k=50. We should choose K = 20 in this case


In [22]:
# Create KMeans Algorithm to cluster the data in 20 groups 
model = KMeans(n_clusters = 20)

# Train KMeans
model.fit(X)

# Get the cluster values for each movie
labels = model.predict(X)

# Put the cluster value back to the dataset
movie_df['cluster'] = labels

# Save it into a new csv file, you can view the result in this csv file
movie_df.sort_values(by=['cluster']).to_csv("MovieCluster.csv")

## Hierarchy Clustering Similar Users


We need to create a new dataframe from the full rating dataset
The new dataframe should contains all the average rating the user previous rating for all the genre

In [23]:
def generate_user_avg_rating_df():
    #genres_list includes ['Action', 'Adventure', 'Animation', 'Children', etc...]
    genres_list = get_movie_genres().values

    # Columns name variable for creating the new dataframe
    columns_name = ["userId"]
    # Create Columns name array
    for genres in genres_list:
        columns_name.append("AVG_" + genres + "_Rating")

    # initialize the dataframe     
    df = pd.DataFrame(columns=columns_name)

    for userId in range(1,full_rating_dataset['userId'].max() + 1):
        row_values = { 'userId': userId }
        for idx , genre in enumerate(genres_list):
            # Getting the user Dataframe for calculating the avg value for this genre
            user_df = full_rating_dataset.loc[(full_rating_dataset["userId"] == userId) & (full_rating_dataset[genre] == 1) ]
            # calculating the avg value for this genre
            avg = user_df["rating"].mean()

            row_values.update( { columns_name[idx + 1] : avg} )
            
        df = df.append( pd.Series(row_values), ignore_index = True )
    df[['userId']] = df[['userId']].astype(int)
    return df.fillna(0)


In [24]:
# generate user avg rating dataframe
user_avg_rating_df = generate_user_avg_rating_df()

user_avg_rating_df

userId  AVG_Action_Rating  AVG_Adventure_Rating  AVG_Animation_Rating  \
0         1           4.636752              4.639752              4.731707   
1         2           3.881579              3.947368              0.000000   
2         3           3.571429              2.727273              0.500000   
3         4           3.162791              4.247059              4.000000   
4         5           3.384615              3.333333              3.833333   
5         6           3.433333              3.982759              4.277778   
6         7           3.574675              3.803109              3.846154   
7         8           3.136364              3.909091              5.000000   
8         9           4.000000              4.500000              4.000000   
9        10           2.257463              3.583333              3.765625   
10       11           3.840580              3.720000              0.000000   
11       12           4.000000              3.000000              3.000000   
12       13           4.617647              4.600000              0.000000   
13       14           3.962963              3.461538              0.000000   
14       15           3.284830              3.667526              3.109091   
15       16           3.559361              3.569444              3.984375   
16       17           4.360377              4.536885              4.300000   
17       18           3.925512              3.792781              3.875000   
18       19           3.568047              3.068966              3.014286   
19       20           3.136986              3.757246              4.323864   
20       21           3.283940              3.541985              3.144737   
21       22           3.185535              2.300000              2.369565   
22       23           3.831579              3.650000              3.619048   
23       24           3.820896              3.786667              4.250000   
24       25           4.964286              4.949541              4.944444   
25       26           3.000000              2.777778              0.000000   
26       27           3.687500              3.301775              3.542857   
27       28           3.527835              3.436306              3.590909   
28       29           4.266667              4.658537              3.500000   
29       30           4.705882              4.793651              4.741935   
..      ...                ...                   ...                   ...   
580     581           4.443878              4.409091              4.113636   
581     582           4.266332              4.103774              3.660714   
582     583           3.000000              3.388889              3.454545   
583     584           3.694118              4.586207              4.909091   
584     585           4.651515              4.687500              4.000000   
585     586           4.538079              4.572131              4.686747   
586     587           4.060606              4.102564              4.250000   
587     588           3.400000              3.000000              3.000000   
588     589           3.428571              3.818182              0.000000   
589     590           3.616302              3.784010              3.889831   
590     591           3.375000              4.754098              4.357143   
591     592           4.053763              4.047619              4.000000   
592     593           3.865854              3.760000              3.187500   
593     594           4.515385              4.316176              4.777778   
594     595           4.000000              4.400000              4.666667   
595     596           3.560144              3.633038              3.991304   
596     597           4.004405              4.178082              4.000000   
597     598           4.806452              3.700000              1.000000   
598     599           3.108553              3.113573              2.967078   
599     600           3.261

In [25]:
%matplotlib inline

from scipy.cluster.hierarchy import linkage, dendrogram
user_X = user_avg_rating_df.iloc[:,1:].values

mergings = linkage(user_X, method='complete')

dendrogram(
    mergings,
    labels = range(0,611),
)

plt.show()

In [26]:
X2 = user_avg_rating_df.iloc[:,1:].values

# Performs K = 1 to 50 for clustering the data
Ks2 = range(1,50)
# Array for saving inertias values for each K Clustering
inertias2 = []

# Loop K times 
for k in Ks2:
    # Create KMeans
    model = KMeans(n_clusters = k)
    # Train KMeans 
    model.fit(X2)
    inertias2.append(model.inertia_)

# Plot inertias values vs K numbers 
plt.ylabel("inertias")
plt.xlabel("Numbers of K")
plt.plot(Ks2,inertias2,'-o')

## From the Grpah above, We can see that the dramatic decrease stop around cluster = 14, So we use 14 to cluster the user group

In [27]:
from scipy.cluster.hierarchy import fcluster
labels = fcluster(mergings, 12.5, criterion = 'distance')

# Put the cluster value back to the dataset
user_avg_rating_df['cluster'] = labels

# Save it into a new csv file, you can view the result in this csv file
user_avg_rating_df.sort_values(by=['cluster']).to_csv("User_Cluster.csv")

labels

array([7, 5, 2, 6, 6, 7, 3, 6, 7, 4, 8, 3, 8, 5, 3, 6, 7, 7, 7, 6, 7, 6,
       6, 3, 3, 8, 7, 6, 7, 3, 6, 6, 7, 5, 6, 8, 6, 6, 7, 6, 7, 7, 6, 2,
       6, 6, 6, 3, 3, 6, 7, 6, 7, 4, 2, 3, 7, 6, 7, 4, 8, 7, 7, 7, 4, 7,
       3, 6, 7, 3, 3, 8, 6, 7, 6, 5, 4, 5, 7, 7, 2, 6, 6, 7, 3, 6, 2, 5,
       6, 6, 7, 3, 6, 6, 6, 7, 3, 3, 6, 6, 3, 6, 7, 7, 7, 3, 5, 6, 6, 8,
       6, 6, 7, 3, 7, 6, 6, 8, 7, 2, 6, 7, 5, 7, 7, 4, 8, 7, 7, 6, 6, 6,
       4, 6, 7, 4, 7, 4, 4, 7, 7, 6, 1, 6, 6, 4, 6, 4, 8, 2, 2, 6, 2, 3,
       6, 7, 3, 2, 4, 7, 2, 6, 2, 8, 6, 7, 7, 7, 6, 4, 6, 6, 4, 6, 1, 6,
       6, 6, 6, 3, 4, 7, 5, 3, 3, 7, 7, 7, 3, 7, 7, 5, 4, 8, 7, 3, 8, 7,
       7, 7, 6, 7, 5, 7, 3, 6, 8, 2, 3, 4, 7, 7, 3, 2, 7, 7, 2, 8, 7, 6,
       7, 6, 6, 3, 2, 6, 7, 3, 6, 4, 4, 7, 6, 6, 6, 2, 4, 8, 7, 6, 6, 5,
       3, 8, 1, 7, 7, 2, 7, 6, 3, 4, 7, 7, 1, 6, 2, 3, 2, 6, 5, 2, 7, 3,
       5, 7, 5, 7, 2, 2, 2, 5, 6, 7, 7, 3, 2, 6, 7, 6, 4, 6, 3, 6, 8, 7,
       6, 7, 6, 7, 3, 6, 2, 7, 5, 3, 8, 6, 8, 7, 6,